In [1]:
import matplotlib.pyplot as plt
import gym
import numpy as np
import torch 
from torch import nn
from torch.autograd import Variable
from torch.nn import functional as F
from torchvision.datasets import MNIST
from torch.utils.data import DataLoader, Dataset
from PIL import Image
import random
from collections import namedtuple
import pdb

In [2]:
torch.cuda.set_device(3)

In [4]:
class MnistSet(Dataset):
    def __init__(self):
        self.MNIST = MNIST('/data/zhuyuanjin/Mnist', download=True)
        pass
    def __len__(self):
        return len(self.MNIST)
    def __getitem__(self, idx):
        img = np.array(self.MNIST[idx][0]).astype(np.float32)
        label = np.array(self.MNIST[idx][1]).astype(np.int32).reshape(1)
        return {'img': img , 'label':label}
dataset = MnistSet()
dataloader = DataLoader(dataset, batch_size=128)

Processing...
Done!


In [13]:
class Network(nn.Module):
    def __init__(self):
        super(Network, self).__init__()
        self.bn = nn.BatchNorm2d(6)
        self.conv1 = nn.Conv2d(in_channels=1, out_channels=6, kernel_size=5, stride=1)
        self.conv2 = nn.Conv2d(in_channels=6, out_channels=12, kernel_size=5, stride=1)
        self.conv3 = nn.Conv2d(in_channels=12, out_channels=24, kernel_size=5,stride=1)
        self.conv4 = nn.Conv2d(in_channels=24, out_channels=64, kernel_size=5,stride=1)
        self.conv5 = nn.Conv2d(in_channels=64, out_channels=96, kernel_size=5,stride=1)
        self.conv6 = nn.Conv2d(in_channels=96, out_channels=128, kernel_size=5,stride=1)
        self.conv7 = nn.Conv2d(in_channels=128, out_channels=256, kernel_size=4,stride=1)
        self.fc1 = nn.Linear(256,128)
        self.fc2 = nn.Linear(128, 32)
        self.head = nn.Linear(32,10)
    def forward(self, x):
        x = x.unsqueeze(1)
        x = self.bn(F.relu(self.conv1(x)))
        x = F.relu(self.conv2(x))
        x = F.relu(self.conv3(x))
        x = F.relu(self.conv4(x))
        x = F.relu(self.conv5(x))
        x = F.relu(self.conv6(x))
        x = F.relu(self.conv7(x))
        x = x.view(x.size(0), -1)
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = F.relu(self.head(x))
        return x

In [14]:
loss_fn = nn.CrossEntropyLoss()
net = Network().cuda()
opt = torch.optim.Adam(net.parameters())

In [ ]:
for epoch in range(10):
    total_loss = 0
    for batch in dataloader:
        x = Variable(batch['img']).cuda()
        y = Variable(batch['label']).cuda().long().squeeze()
        y_pred = net(x)
        loss = loss_fn(y_pred,y)
        opt.zero_grad()
        loss.backward()
        opt.step()
        total_loss += loss.data.cpu().numpy()[0]
    print('epoch %d, total loss %f' %(epoch, total_loss))


epoch 0, total loss 3.461591
epoch 1, total loss 4.597557
epoch 2, total loss 3.752192


In [9]:
Transition = namedtuple('MNIST',['Img','label'])

In [10]:
def Img2Var(img):
    img = np.array(img)
    img = Variable(torch.from_numpy(img)).float().cuda().unsqueeze(0)
    return img

In [11]:
mnist = MNIST('~/Documents/data')

In [12]:
input = tuple(map(Img2Var, Transition(*zip(*mnist)).Img))
input = torch.cat(input)

In [13]:
w = 0
for i in range(60000):
    y_pred = net(Variable(torch.from_numpy(np.array(mnist[i][0]))).float().cuda().unsqueeze(0)).max(1)[1].data.cpu().numpy()
    if y_pred[0] != mnist[i][1]:
        w += 1
print(w)

677


0.008966666666666666

In [2]:
Transition = namedtuple('Transition',
                        ('state', 'action', 'next_state', 'reward', 'terminal'))
class ReplayMemory(object):

    def __init__(self, capacity):
        self.capacity = capacity
        self.memory = []
        self.position = 0

    def push(self, *args):
        """Saves a transition."""
        if len(self.memory) < self.capacity:
            self.memory.append(None)
        self.memory[self.position] = Transition(*args)
        self.position = (self.position + 1) % self.capacity

    def sample(self, batch_size):
        return random.sample(self.memory, batch_size)

    def __len__(self):
        return len(self.memory)



In [3]:
class CartPoleNet(nn.Module):
    def __init__(self):
        super(CartPoleNet, self).__init__()
        self.fc1 = nn.Linear(4, 16)
        self.fc2 = nn.Linear(16, 32)
        self.fc3 = nn.Linear(32, 32)
        self.fc4 = nn.Linear(32, 16)
        self.fc5 = nn.Linear(16, 8)
        self.head = nn.Linear(8, 2)
    def forward(self, x):
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = F.relu(self.fc3(x))
        x = F.relu(self.fc4(x))
        x = F.relu(self.fc5(x))
        output = self.head(x)
        return output
        

In [8]:
class CartPoleAgent:
    def __init__(self):
        self.eps = 0.99
        self.eps_start = 1
        self.eps_end = 0
        self.step = 0
        self.gamma = 0.99
        self.target_net_update = 1000
        self.num_eval_model = 50
        self.env = gym.make('CartPole-v1').unwrapped
        self.memory = ReplayMemory(50000)
        self.policy_net = CartPoleNet()
        self.target_net = CartPoleNet()
        self.target_net.load_state_dict(self.policy_net.state_dict())
        self.use_cuda = torch.cuda.is_available()
        if self.use_cuda:
            self.policy_net = self.policy_net.cuda()
            self.target_net = self.target_net.cuda()
        self.opt = torch.optim.Adam(self.policy_net.parameters())
    def _update_target_net_soft(self):
        for i, key in enumerate(self.target_net.state_dict().keys()):
            self.target_net.state_dict()[key] = self.target_net.state_dict()[key] * (1-self.target_net_update) + self.target_net_update *self.policy_net.state_dict()[key]

    def _save_model(self):
        torch.save(self.policy_net.state_dict(), 'param')

    def _update_target_net_hard(self):
        self.target_net.load_state_dict(self.policy_net.state_dict())

    def epsilon_greedy(self, state, eps):
        if self.use_cuda:
            state = state.cuda()
        if np.random.uniform() < eps:
            action = torch.LongTensor([random.randrange(self.env.action_space.n)]).unsqueeze(0)
        else:
            action = self.policy_net(state).max(1)[1].view(1, 1).data.cpu()
        return action

    def train_epoch(self, batch_size):
        if len(self.memory) < batch_size:
            return
        transitions = self.memory.sample(batch_size)
        batch = Transition(*zip(*transitions))
        state_batch = torch.cat(batch.state)
        reward_batch = torch.cat(batch.reward)
        action_batch = Variable(torch.cat(batch.action))
        next_state_batch = torch.cat(batch.next_state)
        isnot_terminal = torch.from_numpy(np.array(tuple(0. if batch.terminal[i] else 1. for i in range(batch_size)))).unsqueeze(1)
        if self.use_cuda:
            state_batch = state_batch.cuda()
            reward_batch = reward_batch.cuda()
            action_batch = action_batch.cuda()
            next_state_batch = next_state_batch.cuda()
            isnot_terminal = isnot_terminal.cuda()
        qvalues = self.policy_net(state_batch).gather(1, action_batch)
        next_qvalues = self.target_net(next_state_batch).max(1)[0]
        target_values = self.gamma * next_qvalues.unsqueeze(1).data * isnot_terminal.float() + reward_batch
        target_values = Variable(target_values)
        loss_fn = nn.MSELoss()
        loss = loss_fn(qvalues, target_values)
        self.opt.zero_grad()
        loss.backward()
        for param in self.policy_net.parameters():
            param.grad.data.clamp_(-1, 1)
        self.opt.step()
        print('Step %5d , loss %10f, eps %10f' % (self.step, loss.data.cpu().numpy(), self.eps))
        if self.target_net_update > 1 and self.step % self.target_net_update == 0:
            self._update_target_net_hard()
            print('硬更新target_net!!!!!!!!!!!!!!!!!!!!!!!!!')
        if self.target_net_update < 1:
            self._update_target_net_soft()
    

    def fit_model(self, num_steps, batch_size):
        while self.step < num_steps:
            duration = 0
            ob = self.env.reset()
            state = Variable(torch.from_numpy(ob)).unsqueeze(0).float()
            self.eps = self.eps_start - (self.eps_start - self.eps_end) * min(1, self.step / (0.7 * num_steps))
            done = False
            while not done:
                duration = duration + 1
                action = self.epsilon_greedy(state, self.eps)
                ob, r, done, _ = self.env.step(action[0, 0])
                reward = torch.Tensor([[r]])
                next_state = state = Variable(torch.from_numpy(ob)).unsqueeze(0).float()
                self.memory.push(state, action, next_state, reward, done)
                state = next_state
                self.step += 1
                self.train_epoch(batch_size)
            print('这个episode有%d帧' % duration)
        self._save_model()

        

In [ ]:
agent = CartPoleAgent()
agent.fit_model(100000, 128)

WARN: gym.spaces.Box autodetected dtype as <class 'numpy.float32'>. Please provide explicit dtype.
这个episode有25帧
这个episode有12帧
这个episode有32帧
这个episode有16帧
这个episode有26帧
Step   128 , loss   1.010717, eps   0.998414
Step   129 , loss   1.007122, eps   0.998414
Step   130 , loss   1.004368, eps   0.998414
Step   131 , loss   1.001722, eps   0.998414
Step   132 , loss   0.999045, eps   0.998414
Step   133 , loss   0.996327, eps   0.998414
Step   134 , loss   0.993582, eps   0.998414
Step   135 , loss   0.990778, eps   0.998414
Step   136 , loss   0.987952, eps   0.998414
这个episode有25帧
Step   137 , loss   0.986548, eps   0.998057
Step   138 , loss   0.983566, eps   0.998057
Step   139 , loss   0.980560, eps   0.998057
Step   140 , loss   0.977464, eps   0.998057
Step   141 , loss   0.974438, eps   0.998057
Step   142 , loss   0.971055, eps   0.998057
Step   143 , loss   0.964854, eps   0.998057
Step   144 , loss   0.964581, eps   0.998057
Step   145 , loss   0.961106, eps   0.998057
Step   

Step   319 , loss   0.001249, eps   0.995600
Step   320 , loss   0.001788, eps   0.995600
Step   321 , loss   0.001214, eps   0.995600
Step   322 , loss   0.000997, eps   0.995600
Step   323 , loss   0.001231, eps   0.995600
Step   324 , loss   0.000958, eps   0.995600
Step   325 , loss   0.001174, eps   0.995600
Step   326 , loss   0.001156, eps   0.995600
Step   327 , loss   0.001138, eps   0.995600
Step   328 , loss   0.000930, eps   0.995600
Step   329 , loss   0.000951, eps   0.995600
Step   330 , loss   0.000638, eps   0.995600
Step   331 , loss   0.001043, eps   0.995600
Step   332 , loss   0.000703, eps   0.995600
Step   333 , loss   0.000646, eps   0.995600
这个episode有25帧
Step   334 , loss   0.001017, eps   0.995243
Step   335 , loss   0.000857, eps   0.995243
Step   336 , loss   0.000776, eps   0.995243
Step   337 , loss   0.000606, eps   0.995243
Step   338 , loss   0.000762, eps   0.995243
Step   339 , loss   0.000896, eps   0.995243
Step   340 , loss   0.000568, eps   0.995

Step   519 , loss   0.000453, eps   0.992600
Step   520 , loss   0.000343, eps   0.992600
Step   521 , loss   0.000546, eps   0.992600
Step   522 , loss   0.000385, eps   0.992600
Step   523 , loss   0.000234, eps   0.992600
Step   524 , loss   0.000537, eps   0.992600
Step   525 , loss   0.000346, eps   0.992600
Step   526 , loss   0.000300, eps   0.992600
Step   527 , loss   0.000442, eps   0.992600
Step   528 , loss   0.000314, eps   0.992600
Step   529 , loss   0.000396, eps   0.992600
Step   530 , loss   0.000332, eps   0.992600
Step   531 , loss   0.000287, eps   0.992600
Step   532 , loss   0.000364, eps   0.992600
Step   533 , loss   0.000723, eps   0.992600
Step   534 , loss   0.000467, eps   0.992600
Step   535 , loss   0.000302, eps   0.992600
Step   536 , loss   0.000440, eps   0.992600
这个episode有18帧
Step   537 , loss   0.000511, eps   0.992343
Step   538 , loss   0.000733, eps   0.992343
Step   539 , loss   0.000492, eps   0.992343
Step   540 , loss   0.000340, eps   0.992

Step   713 , loss   0.000253, eps   0.989857
Step   714 , loss   0.000150, eps   0.989857
Step   715 , loss   0.000211, eps   0.989857
Step   716 , loss   0.000293, eps   0.989857
Step   717 , loss   0.000261, eps   0.989857
Step   718 , loss   0.000102, eps   0.989857
Step   719 , loss   0.000371, eps   0.989857
Step   720 , loss   0.000318, eps   0.989857
Step   721 , loss   0.000548, eps   0.989857
这个episode有11帧
Step   722 , loss   0.000271, eps   0.989700
Step   723 , loss   0.000298, eps   0.989700
Step   724 , loss   0.000482, eps   0.989700
Step   725 , loss   0.000382, eps   0.989700
Step   726 , loss   0.000319, eps   0.989700
Step   727 , loss   0.000528, eps   0.989700
Step   728 , loss   0.000383, eps   0.989700
Step   729 , loss   0.000208, eps   0.989700
Step   730 , loss   0.000505, eps   0.989700
Step   731 , loss   0.000477, eps   0.989700
Step   732 , loss   0.000199, eps   0.989700
Step   733 , loss   0.000345, eps   0.989700
Step   734 , loss   0.000262, eps   0.989

Step   912 , loss   0.000249, eps   0.987343
Step   913 , loss   0.000152, eps   0.987343
Step   914 , loss   0.000318, eps   0.987343
Step   915 , loss   0.000233, eps   0.987343
Step   916 , loss   0.000424, eps   0.987343
Step   917 , loss   0.000251, eps   0.987343
Step   918 , loss   0.000222, eps   0.987343
Step   919 , loss   0.000245, eps   0.987343
Step   920 , loss   0.000276, eps   0.987343
Step   921 , loss   0.000275, eps   0.987343
Step   922 , loss   0.000277, eps   0.987343
Step   923 , loss   0.000433, eps   0.987343
Step   924 , loss   0.000604, eps   0.987343
Step   925 , loss   0.000194, eps   0.987343
Step   926 , loss   0.000127, eps   0.987343
Step   927 , loss   0.000270, eps   0.987343
Step   928 , loss   0.000398, eps   0.987343
Step   929 , loss   0.000463, eps   0.987343
Step   930 , loss   0.000203, eps   0.987343
Step   931 , loss   0.000299, eps   0.987343
Step   932 , loss   0.000313, eps   0.987343
Step   933 , loss   0.000456, eps   0.987343
Step   934

...

Step 84403 , loss   0.482981, eps   0.000000
Step 84404 , loss   0.135782, eps   0.000000
Step 84405 , loss   0.249722, eps   0.000000
Step 84406 , loss   0.612170, eps   0.000000
这个episode有35帧
Step 84407 , loss   0.345686, eps   0.000000
Step 84408 , loss   0.263664, eps   0.000000
Step 84409 , loss   0.070001, eps   0.000000
Step 84410 , loss   0.197960, eps   0.000000
Step 84411 , loss   0.124947, eps   0.000000
Step 84412 , loss   0.560378, eps   0.000000
Step 84413 , loss   0.116563, eps   0.000000
Step 84414 , loss   0.030253, eps   0.000000
Step 84415 , loss   0.045627, eps   0.000000
这个episode有9帧
Step 84416 , loss   0.239960, eps   0.000000
Step 84417 , loss   0.073615, eps   0.000000
Step 84418 , loss   1.377478, eps   0.000000
Step 84419 , loss   0.179423, eps   0.000000
Step 84420 , loss   1.919250, eps   0.000000
Step 84421 , loss   0.291450, eps   0.000000
Step 84422 , loss   0.244567, eps   0.000000
Step 84423 , loss   0.899481, eps   0.000000
Step 84424 , loss   1.369388

Step 84633 , loss   0.162728, eps   0.000000
Step 84634 , loss   0.616319, eps   0.000000
Step 84635 , loss   2.695115, eps   0.000000
Step 84636 , loss   0.017967, eps   0.000000
Step 84637 , loss   1.331130, eps   0.000000
这个episode有10帧
Step 84638 , loss   0.477568, eps   0.000000
Step 84639 , loss   0.315533, eps   0.000000
Step 84640 , loss   0.385600, eps   0.000000
Step 84641 , loss   0.257728, eps   0.000000
Step 84642 , loss   0.043115, eps   0.000000
Step 84643 , loss   0.550261, eps   0.000000
Step 84644 , loss   0.442184, eps   0.000000
Step 84645 , loss   0.850666, eps   0.000000
这个episode有8帧
Step 84646 , loss   0.020695, eps   0.000000
Step 84647 , loss   0.042055, eps   0.000000
Step 84648 , loss   0.187154, eps   0.000000
Step 84649 , loss   0.150446, eps   0.000000
Step 84650 , loss   0.789326, eps   0.000000
Step 84651 , loss   0.975743, eps   0.000000
Step 84652 , loss   0.904252, eps   0.000000
Step 84653 , loss   0.055657, eps   0.000000
Step 84654 , loss   0.255203

Step 84863 , loss   2.457518, eps   0.000000
Step 84864 , loss   0.301227, eps   0.000000
Step 84865 , loss   0.839731, eps   0.000000
Step 84866 , loss   0.142803, eps   0.000000
Step 84867 , loss   1.912068, eps   0.000000
Step 84868 , loss   0.363196, eps   0.000000
Step 84869 , loss   1.308357, eps   0.000000
Step 84870 , loss   2.440701, eps   0.000000
这个episode有9帧
Step 84871 , loss   1.619971, eps   0.000000
Step 84872 , loss   0.914181, eps   0.000000
Step 84873 , loss   0.505932, eps   0.000000
Step 84874 , loss   0.556196, eps   0.000000
Step 84875 , loss   0.457210, eps   0.000000
Step 84876 , loss   0.615345, eps   0.000000
Step 84877 , loss   1.291233, eps   0.000000
Step 84878 , loss   0.341034, eps   0.000000
Step 84879 , loss   0.361447, eps   0.000000
这个episode有9帧
Step 84880 , loss   1.697472, eps   0.000000
Step 84881 , loss   0.045555, eps   0.000000
Step 84882 , loss   1.264619, eps   0.000000
Step 84883 , loss   0.829552, eps   0.000000
Step 84884 , loss   0.941887,

Step 85092 , loss   0.829938, eps   0.000000
Step 85093 , loss   0.228343, eps   0.000000
Step 85094 , loss   0.101273, eps   0.000000
Step 85095 , loss   0.308067, eps   0.000000
Step 85096 , loss   0.312269, eps   0.000000
Step 85097 , loss   0.200034, eps   0.000000
Step 85098 , loss   0.323338, eps   0.000000
这个episode有14帧
Step 85099 , loss   0.076219, eps   0.000000
Step 85100 , loss   1.987510, eps   0.000000
Step 85101 , loss   1.246062, eps   0.000000
Step 85102 , loss   0.133508, eps   0.000000
Step 85103 , loss   0.098266, eps   0.000000
Step 85104 , loss   0.346424, eps   0.000000
Step 85105 , loss   0.239895, eps   0.000000
Step 85106 , loss   0.088550, eps   0.000000
Step 85107 , loss   0.125125, eps   0.000000
这个episode有9帧
Step 85108 , loss   0.063520, eps   0.000000
Step 85109 , loss   4.733175, eps   0.000000
Step 85110 , loss   0.251170, eps   0.000000
Step 85111 , loss   0.309677, eps   0.000000
Step 85112 , loss   1.231031, eps   0.000000
Step 85113 , loss   0.418403

Step 85321 , loss   0.362345, eps   0.000000
这个episode有9帧
Step 85322 , loss   0.653206, eps   0.000000
Step 85323 , loss   0.761992, eps   0.000000
Step 85324 , loss   0.164036, eps   0.000000
Step 85325 , loss   0.499131, eps   0.000000
Step 85326 , loss   1.386185, eps   0.000000
Step 85327 , loss   0.364249, eps   0.000000
Step 85328 , loss   0.251860, eps   0.000000
Step 85329 , loss   0.093270, eps   0.000000
Step 85330 , loss   0.101642, eps   0.000000
这个episode有9帧
Step 85331 , loss   0.096510, eps   0.000000
Step 85332 , loss   0.059686, eps   0.000000
Step 85333 , loss   0.137791, eps   0.000000
Step 85334 , loss   0.317196, eps   0.000000
Step 85335 , loss   0.041341, eps   0.000000
Step 85336 , loss   0.045599, eps   0.000000
Step 85337 , loss   0.049397, eps   0.000000
Step 85338 , loss   0.347178, eps   0.000000
Step 85339 , loss   0.220119, eps   0.000000
这个episode有9帧
Step 85340 , loss   0.088011, eps   0.000000
Step 85341 , loss   0.111832, eps   0.000000
Step 85342 , los

In [26]:
env = gym.make('CartPole-v0').unwrapped
env.reset()

WARN: gym.spaces.Box autodetected dtype as <class 'numpy.float32'>. Please provide explicit dtype.


array([ 0.04314151, -0.00167103, -0.00695013,  0.04924609])

In [27]:
done = False
while not done:
    ob, r, done, _ = env.step(env.action_space.sample())
    print(r, done)

1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 False
1.0 True


In [31]:
np.array([True, True]) == False

array([False, False])